### Imports

In [1]:
import numpy as np
import pandas as pd
import importlib
import os

import findatree.io as io
import findatree.transformations as transformations
import findatree.interactive as interactive
import findatree.geo_to_image as geo_to_image
import findatree.segmentation as segmentation
import findatree.photometric as photometric

from bokeh.plotting import show, save
from bokeh.io import output_notebook, output_file 
output_notebook()

Loading BokehJS ...

### Definitions

In [12]:
tnr = 11090

dir_names=[]
dir_names.extend([r'C:\Data\lwf\WZE-UAV-2020\DSMs'])
dir_names.extend([r'C:\Data\lwf\WZE-UAV-2020\DTMs'])
dir_names.extend([r'C:\Data\lwf\WZE-UAV-2020\Orthos'])
dir_names.extend([r'C:\Data\lwf\WZE-UAV-2020\Kronen'])


dir_name_hdf5 = r"C:\Data\lwf\processed\2020\hdf5"
dir_name_html = r"C:\Data\lwf\analysis\px-wise_correlation\html"

### Load channels from .tif

In [57]:
importlib.reload(geo_to_image)

params_channels = {
    'tnr': tnr,
    'px_width_reproject': 0.2,
    'downscale': 0,
}

# Load, reproject, normalize & downscale rasters
channels, params_channels = geo_to_image.channels_load(dir_names, params_channels)

# Save repojected rasters as channels in .hdf5
io.channels_to_hdf5(channels, params_channels, dir_name = dir_name_hdf5)

### Load channels from .hdf5

In [27]:
importlib.reload(io)

# Load data
data, params_data = io.load_hdf5(
    path = os.path.join(dir_name_hdf5, f"tnr{tnr}.hdf5"),
    groups = ['channels'],
    )

# Assign channels
channels = data['channels']
params_channels = params_data['channels']
del data, params_data

### Load human crowns

In [28]:
importlib.reload(io)

# Load 'hand selected' human crowns
crowns_human, params_crowns_human = io.load_shapefile(
    dir_names,
    params_channels,
    remove_outliers = True,
    )

# Save crowns in .hdf5
# io.crowns_to_hdf5(crowns_human, params_crowns_human, dir_name = dir_name_hdf5)

-----------
Parameters:
  affine                        : [[ 2.00000000e-01  0.00000000e+00  7.90713528e+05]
 [ 0.00000000e+00 -2.00000000e-01  5.45189531e+06]
 [ 0.00000000e+00  0.00000000e+00  1.00000000e+00]]
  date_time_polygons            : 220824-122330
  date_time_terrestrial         : 220824-122330
  number_crowns                 : 39
  origin                        : human
  path_shapes                   : C:\Data\lwf\WZE-UAV-2020\Kronen\Tnr_11090_Kr.shp
  shape                         : [1853 1729]
  tnr                           : 11090


### Add photometric features to human crowns

In [29]:
importlib.reload(photometric)
importlib.reload(io)

# Add photometric features to human crowns
photometric.crowns_add_features(
    channels,
    params_channels,
    crowns_human,
    params_crowns_human,
)

# Save crowns in .hdf5
# io.crowns_to_hdf5(crowns_human, params_crowns_human, dir_name = dir_name_hdf5)

### View human crown features as DataFrame

In [73]:
df = pd.merge(
    left = pd.DataFrame(crowns_human['features']['photometric']),
    right = pd.DataFrame(crowns_human['features']['terrestrial']),
    how= 'inner',
    on = ['id'],
    )

df.query('ba > 0')[['id', 'ba', 'kkl', 'nbv','sst', 'perc25_brightest_ndvi','max_chm','elipticity']]

eccentricity


### Generate watershed crowns

In [61]:
importlib.reload(segmentation)
importlib.reload(io)

params_crowns_water = {
    # 'thresh_channel': 'chm',
    # 'thresh_blur': True,
    # 'thresh_width':30,
    # 'thresh_downscale': 2,
    # 'water_channel':'chm',
    # 'water_hole_min_area': 0.2,
}

crowns_water, params_crowns_water = segmentation.watershed(
    channels,
    params_channels,
    params_crowns_water,
)

io.crowns_to_hdf5(crowns_water, params_crowns_water, dir_name = dir_name_hdf5)

-----------
Parameters:
  affine                        : [[ 2.00000000e-01  0.00000000e+00  7.61562237e+05]
 [ 0.00000000e+00 -2.00000000e-01  5.37866511e+06]
 [ 0.00000000e+00  0.00000000e+00  1.00000000e+00]]
  date_time_polygons            : 220804-135821
  number_crowns                 : 4585
  origin                        : water
  shape                         : [1722 1695]
  thresh_blur                   : False
  thresh_channel                : light
  thresh_downscale              : 1
  thresh_global_chm_lower       : 5
  thresh_global_chm_upper       : 40
  thresh_global_ndvi            : 0.3
  thresh_px_width               : 0.4
  thresh_shape                  : (861, 848)
  thresh_width                  : 30
  tnr                           : 6462
  water_channel                 : light
  water_downscale               : 0
  water_hole_min_area           : 0.0
  water_label_min_area          : 0.2
  water_peak_dist               : 1.2
  water_px_width                : 0.2
 

### Add photometric features to watershed crowns

In [52]:
importlib.reload(photometric)
importlib.reload(io)

# Add photometric features to human crowns
photometric.crowns_add_features(
    channels,
    params_channels,
    crowns_water,
    params_crowns_water,
)

# Save crowns in .hdf5
io.crowns_to_hdf5(crowns_water, params_crowns_water, dir_name = dir_name_hdf5)

### Plotting

In [78]:
importlib.reload(interactive)

plt = interactive.Plotter()
plt.width = 400
plt.channels_downscale = 1
plt.show_features=[
    'id',
    'ba', 'kkl', 'sst', 'nbv',
    'eccentricity', 'mean_chm', 
]

plt.add_channels(channels, params_channels)

plt.figures_add_rgb()
# plt.figures_add_gray('lbp')

# plt.togglers_add_crowns(crowns_water, params_crowns_water)
plt.togglers_add_crowns(crowns_human, params_crowns_human)

layout = plt.create_layout()

In [79]:
show(layout)

# output_file(os.path.join(dir_name_html, f"tnr{tnr}.html"), mode='inline')
# save(layout)